In [1]:
import ray
ray.shutdown()
import os
os.environ["RAY_ML_DEV"] = "1"

In [2]:
SMOKE_TEST = 1

In [3]:
import ray
import torch
import pytorch_lightning as pl
import torch.nn.functional as F
from torch.utils.data import DataLoader, random_split
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from datasets import load_dataset
import numpy as np

/home/ray/anaconda3/lib/python3.8/site-packages/xgboost/compat.py:31: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  from pandas import MultiIndex, Int64Index


In [4]:
dataset = load_dataset('glue', 'cola')
tokenizer = AutoTokenizer.from_pretrained('bert-base-cased')
num_classes = 2 # positive or negative sentiment

Reusing dataset glue (/home/ray/.cache/huggingface/datasets/glue/cola/1.0.0/dacbe3125aa31d7f70367a07a8a9e72a5a0bfeb5fc42e75c9db75b96da6053ad)


  0%|          | 0/3 [00:00<?, ?it/s]

In [5]:
ray_datasets = {
    "train": ray.data.from_torch(dataset["train"]),
    "val": ray.data.from_torch(dataset["validation"]),
    "test": ray.data.from_torch(dataset["test"])
}

find: ‘.git’: No such file or directory
2023-03-27 17:57:07,390	INFO worker.py:1413 -- Connecting to existing Ray cluster at address: 10.0.18.215:6379...
2023-03-27 17:57:07,398	INFO worker.py:1601 -- Connected to Ray cluster. View the dashboard at https://console.anyscale-staging.com/api/v2/sessions/ses_lakhijrn6mdv9hqpld5trwzlxz/services?redirect_to=dashboard 
2023-03-27 17:57:08,030	INFO packaging.py:346 -- Pushing file package 'gcs://_ray_pkg_1d251ada32aca67a7b5d33a48a9487b5.zip' (16.47MiB) to Ray cluster...
2023-03-27 17:57:08,192	INFO packaging.py:359 -- Successfully pushed file package 'gcs://_ray_pkg_1d251ada32aca67a7b5d33a48a9487b5.zip'.


In [18]:
def collate_fn(batch):
    encoded_sent = tokenizer(batch['sentence'].tolist(), truncation=True, padding=True, return_tensors='pt')
    batch["input_ids"] = encoded_sent["input_ids"].cuda()
    batch["attention_mask"] = encoded_sent["attention_mask"].cuda()
    batch["label"] = torch.LongTensor(batch["label"]).cuda()
    batch.pop("sentence")
    return batch

# for batch in ray_datasets["train"].iter_torch_batches(batch_size=3, collate_fn=collate):
#     input()

In [19]:
class SentimentModel(pl.LightningModule):
    def __init__(self, lr=2e-5, eps=1e-8):
        super().__init__()
        self.lr = lr
        self.eps = eps
        self.num_classes = 2
        self.model = AutoModelForSequenceClassification.from_pretrained('bert-base-cased', num_labels=self.num_classes)

    def forward(self, input_ids, attention_mask):
        outputs = self.model(input_ids, attention_mask=attention_mask)
        logits = outputs.logits
        return logits

    def training_step(self, batch, batch_idx):
        input_ids, attention_mask, label = batch["input_ids"], batch["attention_mask"], batch["label"]
        logits = self.forward(input_ids, attention_mask)
        loss = F.cross_entropy(logits.view(-1, self.num_classes), labels)
        self.log('train_loss', loss)
        return loss

    def validation_step(self, batch, batch_idx):
        input_ids, attention_mask, labels = batch["input_ids"], batch["attention_mask"], batch["label"]
        logits = self.forward(input_ids, attention_mask)
        loss = F.cross_entropy(logits.view(-1, self.num_classes), labels)
        preds = torch.argmax(logits, dim=1)
        acc = torch.sum(preds == labels).float() / len(preds)
        self.log('val_loss', loss)
        self.log('val_accuracy', acc)

    def configure_optimizers(self):
        return torch.optim.AdamW(self.parameters(), lr=self.lr, eps=self.eps)


In [20]:
from ray.train.lightning import LightningTrainer, LightningConfigBuilder
from ray.air.config import RunConfig, ScalingConfig, CheckpointConfig
import ray.tune as tune


lightning_config = (
    LightningConfigBuilder()
    .module(cls=SentimentModel, lr=tune.loguniform(1e-3, 1e-5), eps=1e-8)
    .trainer(max_epochs=3, accelerator="gpu")
    .build()
)

datasets_iter_config = {"batch_size": tune.choice([16, 32, 64]), "collate_fn": convert_numpy_to_tensor}

run_config = RunConfig(
    name="ptl-advanced-example",
    checkpoint_config=CheckpointConfig(
        num_to_keep=2,
        checkpoint_score_attribute="val_accuracy",
        checkpoint_score_order="max",
    ),
)

scaling_config = ScalingConfig(
    num_workers=2, use_gpu=True, resources_per_worker={"CPU": 1, "GPU": 1}
)

trainer = LightningTrainer(
    datasets=ray_datasets,
    scaling_config=scaling_config
)


2023-03-27 18:30:21,576	INFO instantiator.py:21 -- Created a temporary directory at /tmp/tmpbdmmxvqv
2023-03-27 18:30:21,577	INFO instantiator.py:76 -- Writing /tmp/tmpbdmmxvqv/_remote_module_non_scriptable.py


NameError: name 'convert_numpy_to_tensor' is not defined


(pid=gcs_server)                                                       [2023-03-27 20:00:54,655 E 3035 3067] (gcs_server) ray_syncer-inl.h:305: [1] Failed to read the message from: 4038e23f6ce5fb85e429bdf477059df9a62040ba71db50f792b5d2f6

output: 199 queued 1:   0%|          | 1/200 [1:52:28<373:01:48, 6748.28s/it]


(autoscaler +2h7m18s) Tip: use `ray status` to view detailed cluster status. To disable these messages, set RAY_SCHEDULER_EVENTS=0.
(autoscaler +2h7m18s) Resized to 16 CPUs, 1 GPUs.
(autoscaler +2h7m18s) Failed to launch 1 node(s) of type worker-node-type-0. (InsufficientInstanceCapacity): We currently do not have sufficient g4dn.4xlarge capacity in the Availability Zone you requested (us-west-2a). Our system will be working on provisioning additional capacity. You can currently get g4dn.4xlarge capacity by not specifying an Availability Zone in your request or choosing us-west-2b, us-west-2c.



output: 199 queued 1:   0%|          | 1/200 [1:54:10<378:40:52, 6850.52s/it]


...


output: 199 queued 1:   0%|          | 1/200 [2:43:05<540:56:52, 9785.99s/it]


(autoscaler +2h56m19s) Adding 1 node(s) of type worker-node-type-0.



output: 199 queued 1:   0%|          | 1/200 [2:43:11<541:13:44, 9791.08s/it]


(autoscaler +2h57m19s) Resized to 32 CPUs, 2 GPUs.



output: 199 queued 1:   0%|          | 1/200 [2:44:11<544:33:37, 9851.35s/it]

In [32]:
from ray.tune.schedulers import PopulationBasedTraining


mutation_lightning_config = (
    LightningConfigBuilder()
    .module(
        lr=tune.loguniform(1e-3, 1e-5),
    )
    .build()
)

tuner = tune.Tuner(
    trainer,
    param_space={"lightning_config": lightning_config, "datasets_iter_config": datasets_iter_config},
    run_config=ray.air.RunConfig(
        name="release-tuner-test",
        verbose=2,
        checkpoint_config=CheckpointConfig(
            num_to_keep=2,
            checkpoint_score_attribute="val_accuracy",
            checkpoint_score_order="max",
        ),
    ),
    tune_config=tune.TuneConfig(
        metric="val_accuracy",
        mode="max",
        num_samples=4,
        scheduler=PopulationBasedTraining(
            time_attr="training_iteration",
            hyperparam_mutations={"lightning_config": mutation_lightning_config},
            perturbation_interval=1,
        ),
    ),
)

In [33]:
# tuner.fit()

In [34]:
lightning_config = (
    LightningConfigBuilder()
    .module(cls=SentimentModel, lr=1e-5, eps=1e-8)
    .trainer(max_epochs=3, accelerator="gpu")
    .build()
)

datasets_iter_config = {"batch_size": 16, "collate_fn": convert_numpy_to_tensor}

single_trainer = LightningTrainer(
    lightning_config=lightning_config,
    datasets=ray_datasets,
    scaling_config=scaling_config,
    datasets_iter_config=datasets_iter_config,
    preprocessor=preprocessor,
)

In [35]:
result = single_trainer.fit()

                                                                                                                                                               
                                                                                                                

                                                                                                                                 


                                                                                                



                                                                                                                                                 




                                                                                                  





                                                                                                                   






(pid=295992)                                                                       /home/ray/anaconda3/lib/python3.8/s

(RayTrainWorker pid=296376) collate_fn =  <function convert_numpy_to_tensor at 0x7f89255aa940>
(RayTrainWorker pid=296376) dtypes =  None
(RayTrainWorker pid=296376) device =  None










(pid=296376) Resource usage vs limits 0:   0%|          | 0/1 [00:00<?, ?it/s]








(pid=296376) BatchMapper 1:   0%|          | 0/200 [00:00<?, ?it/s]









(pid=296376) RandomizeBlockOrder 2:   0%|          | 0/200 [00:00<?, ?it/s]










(pid=296376) Output 3:   0%|          | 0/200 [00:00<?, ?it/s]







(pid=296376) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 0.0 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [00:00<?, ?it/s]










(pid=73616, ip=10.0.3.198)ued 3:   0%|          | 0/200 [00:00<?, ?it/s] Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [11:24<?, ?it/s]
(pid=73616, ip=10.0.3.198) BatchMapper: 0 active, 0 queued 1: 100%|██████████| 200/200 [11:24<00:00, 102.25it/s]

(pid=73616, ip=10.0.3.198) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2: 100%|██████████| 200/200 [11:24<00:00,  2.18s/it]


(pid=73616, ip=10.0.3.198) output: 199 queued 3:   4%|▎         | 

(RayTrainWorker pid=93624, ip=10.0.3.198) collate_fn =  <function convert_numpy_to_tensor at 0x7fcb6d4d9940>
(RayTrainWorker pid=93624, ip=10.0.3.198) dtypes =  None
(RayTrainWorker pid=93624, ip=10.0.3.198) device =  None














(pid=93624, ip=10.0.3.198) Resource usage vs limits 0:   0%|          | 0/1 [00:00<?, ?it/s]












(pid=93624, ip=10.0.3.198) BatchMapper 1:   0%|          | 0/200 [00:00<?, ?it/s]













(pid=93624, ip=10.0.3.198) RandomizeBlockOrder 2:   0%|          | 0/200 [00:00<?, ?it/s]














(pid=93624, ip=10.0.3.198) Output 3:   0%|          | 0/200 [00:00<?, ?it/s]











(pid=93624, ip=10.0.3.198) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 0.0 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [00:00<?, ?it/s]














(pid=93624, ip=10.0.3.198) output: 0 queued 3:   0%|          | 0/200 [00:00<?, ?it/s]












(pid=93624, ip=10.0.3.198) BatchMapper: 32 active, 168 queued 1:   0%|          | 0/200 [00:00<?, ?it/s]













(pid=73616, ip=10.0.3.198) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2:   0%|          | 0/200 [00:00<?, ?it/s] Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_me

...

(pid=73616, ip=10.0.3.198) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [25:07<?, ?it/s]
(pid=73616, ip=10.0.3.198) BatchMapper: 0 active, 0 queued 1: 100%|██████████| 200/200 [25:07<00:00, 102.25it/s]

(pid=73616, ip=10.0.3.198) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2: 100%|██████████| 200/200 [25:07<00:00,  2.18s/it]


(pid=73616, ip=10.0.3.198) output: 199 queued 3:   4%|▎         | 7/200 [25:07<12:33,  3.91s/it]



(pid=208889) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [25:07<?, ?it/s]




(pid=208889) BatchMapper: 0 active, 0 queued 1: 100%|██████████| 200/200 [25:07<00:00, 124.06it/s]





(pid=208889) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2: 100%|██████████| 200/200 [25:07<00:00,  3.38s/it]






(pid=208889) output: 199 queued 3:   4%|▍         | 8/200 [25:07<11:56,  3.73s/it]







(pid=296376) Resource usage 

(RayTrainWorker pid=296376) 100


(pid=73616, ip=10.0.3.198) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [25:09<?, ?it/s]
(pid=73616, ip=10.0.3.198) BatchMapper: 0 active, 0 queued 1: 100%|██████████| 200/200 [25:08<00:00, 102.25it/s]

(pid=73616, ip=10.0.3.198) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2: 100%|██████████| 200/200 [25:08<00:00,  2.18s/it]


(pid=73616, ip=10.0.3.198) output: 199 queued 3:   4%|▎         | 7/200 [25:08<12:33,  3.91s/it]



(pid=208889) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [25:09<?, ?it/s]




(pid=208889) BatchMapper: 0 active, 0 queued 1: 100%|██████████| 200/200 [25:09<00:00, 124.06it/s]





(pid=208889) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2: 100%|██████████| 200/200 [25:09<00:00,  3.38s/it]






(pid=208889) output: 199 queued 3:   4%|▍         | 8/200 [25:09<11:56,  3.73s/it]







(pid=296376) Resource usage 

(RayTrainWorker pid=93624, ip=10.0.3.198) 100


(pid=73616, ip=10.0.3.198) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [25:09<?, ?it/s]
(pid=73616, ip=10.0.3.198) BatchMapper: 0 active, 0 queued 1: 100%|██████████| 200/200 [25:09<00:00, 102.25it/s]

(pid=73616, ip=10.0.3.198) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2: 100%|██████████| 200/200 [25:09<00:00,  2.18s/it]


(pid=73616, ip=10.0.3.198) output: 199 queued 3:   4%|▎         | 7/200 [25:09<12:33,  3.91s/it]



(pid=208889) Resource usage vs limits: 0.0/32.0 CPU, 0.0/2.0 GPU, 97.38 MiB/8.57 GiB object_store_memory 0:   0%|          | 0/1 [25:09<?, ?it/s]




(pid=208889) BatchMapper: 0 active, 0 queued 1: 100%|██████████| 200/200 [25:09<00:00, 124.06it/s]





(pid=208889) RandomizeBlockOrder: 0 active, 0 queued, 0 output 2: 100%|██████████| 200/200 [25:09<00:00,  3.38s/it]






(pid=208889) output: 199 queued 3:   4%|▍         | 8/200 [25:09<11:56,  3.73s/it]







(pid=296376) Resource usage 

In [ ]:
result

Result(
  metrics={'_report_on': 'train_epoch_end', 'train_loss': 0.7121134400367737, 'train_loss_step': 0.6841170787811279, 'val_loss': 0.6932439208030701, 'val_accuracy': 0.5, 'train_loss_epoch': 0.7121134400367737, 'epoch': 2, 'step': 2346, 'should_checkpoint': True, 'done': True, 'trial_id': 'c0189_00000', 'experiment_tag': '0'},
  path='/home/ray/ray_results/LightningTrainer_2023-03-27_13-55-48/LightningTrainer_c0189_00000_0_2023-03-27_13-55-50',
  checkpoint=LightningCheckpoint(local_path=/home/ray/ray_results/LightningTrainer_2023-03-27_13-55-48/LightningTrainer_c0189_00000_0_2023-03-27_13-55-50/checkpoint_000002)
)